# Loading env

In [2]:
from os import listdir
from os.path import isfile, join

path = "E://dump"

dump_files = listdir(path)

import pandas as pd
import numpy as np

# Finding out open-source repos

In [ ]:
df_project_members = pd.read_csv(join(path, 'project_members.csv'), names=["repo_id", "user_id", "created_at"])

df_count_members = df_project_members.groupby("repo_id", as_index=False)["user_id"].count()

df_count_members = df_count_members[df_count_members["user_id"]>10] #gráfico de barras com intervalos

df_open_source_members  = df_project_members.loc[(df_project_members['repo_id'].isin(df_count_members['repo_id']))]



# Gettint commits from open-source repos

In [ ]:
chunks_commits = pd.read_csv(join(path, 'commits.csv'), names=["id", "sha", "author_id", "commiter_id", "project_id", "created_at"], chunksize=5000000)

for i, chunk in range(chunks_commits):
       df_commit = chunk[chunk['project_id'].isin(df_project_members['repo_id'])]
       df_commit.to_csv(join(path, f'open_source/open_source_commits_{i}.csv'), index_label='row_index')

# Fiding out who is begginer

In [3]:
def get_min_date_row(group):
    min_row = group.loc[group['created_at'].idxmin()]
    return min_row
    
dump_open_source_files = listdir(join(path, 'open_source'))

first_user_commit_by_chunks = []
for i, file in enumerate(dump_open_source_files):
    df_commit = pd.read_csv(join(path,'open_source',file))
    df_commit["created_at"] = pd.to_datetime(df_commit["created_at"])
    first_user_commit_by_chunks.append(df_commit.groupby('author_id').apply(get_min_date_row).reset_index(drop=True))

df_first_user_commit = pd.concat(first_user_commit_by_chunks)

df_first_user_contrib = df_first_user_commit.groupby('author_id').apply(get_min_date_row).reset_index(drop=True)

In [ ]:
df_first_user_contrib.to_csv('first_user_contrib.csv', index_label='row_index')

# Starting target dataframe

In [3]:
df_first_user_contrib = pd.read_csv('first_user_contrib.csv')

df_project_members = pd.read_csv(join(path, 'project_members.csv'), names=["repo_id", "user_id", "created_at"])


In [4]:
df_contrib_x_onboard = df_project_members.merge(df_first_user_contrib, left_on=['repo_id', 'user_id'], right_on=['project_id', 'author_id'],  how='inner', suffixes=['_members', '_commits'])


In [ ]:
df_onboardings = df_contrib_x_onboard[['repo_id', 'user_id', 'created_at_members']]
df_onboardings = df_onboardings.rename(columns={'created_at_members': 'onboarding_date'})

# Organizing each repo on its own file

In [14]:
dump_open_source_files = listdir(join(path, 'open_source'))

#df_onboardings = pd.read_csv("onboarding.csv", index_col=0)


repos = df_onboardings['repo_id'].unique()

In [15]:
repos_commits = {}

for repo in repos:
        repos_commits[repo] = []

repos_commits['failed'] = []

for i, file in enumerate(dump_open_source_files):
        print("file: ", i)
        chunk = pd.read_csv(join(path,'open_source', file), )
        chunk_repos = chunk['project_id'].unique()
        for repo in chunk_repos:
                try:
                        repos_commits[repo].append(chunk[chunk['project_id'] == repo])
                except:
                        repos_commits['failed'].append(repo)


import logging

for repo in repos_commits:
    try:
        if repo != 'failed':
            df_repo_commits = pd.concat(repos_commits[repo])
            df_repo_commits.to_csv(join('repos_commits', 'repos_commits_{0}.csv'.format(repo)), index_label='row_index')
    except Exception as e:
        print(repo)        
        logging.exception(e)

# First, Last and Total Commits

In [ ]:
calc_commits_dict = []


def get_total_commits(row):
    repo_id = row['repo_id']
    date = row['onboarding_date']
    user_id = row['user_id']

    project_commits = pd.read_csv(join('repos_commits', 'repos_commits_{0}.csv'.format(repo_id)))
    project_commits['created_at'] = pd.to_datetime(project_commits['created_at'], format='%Y-%m-%d %H:%M:%S')

    project_commits = project_commits.loc[project_commits['created_at'] < pd.to_datetime(date)]

    total_commits = project_commits.shape[0]
    first_commits=project_commits['created_at'].min()
    last_commits=project_commits['created_at'].max()
    
    dict = {'repo_id': repo_id, 'user_id':user_id,'total_commits': total_commits, 'first_commit': first_commits, 'last_commit': last_commits }

    calc_commits_dict.append(dict)

    
    
df_onboardings.apply(get_total_commits, axis=1)   

0         None
1         None
2         None
3         None
4         None
          ... 
162616    None
162617    None
162618    None
162619    None
162620    None
Length: 162621, dtype: object

In [28]:
df_calc_commits = pd.DataFrame(calc_commits_dict)

In [33]:
df_onboardings = df_onboardings.merge(df_calc_commits, left_on=['repo_id', 'user_id'], right_on=['repo_id', 'user_id'],  how='inner')


# Total members on integration date

In [35]:
#df_onboardings = pd.read_csv('onboarding_old.csv')
#repos = df_onboardings['repo_id'].unique()
#df_project_members = pd.read_csv(join(path,"project_members.csv"), names=["repo_id", "user_id", "created_at"])

#df_project_members = df_project_members[df_project_members['repo_id'].isin(repos)]

df_project_members['created_at'] = pd.to_datetime(df_project_members['created_at'])


In [ ]:
def get_total_joinings(date, project):
    this_project_members_before_integration = df_project_members.loc[(df_project_members['created_at'] < pd.to_datetime(date)) & (df_project_members['repo_id'] == project)]
    return len(this_project_members_before_integration["user_id"].unique())

In [37]:
df_onboardings["project_members"] = df_onboardings.apply(lambda x: get_total_joinings(x['onboarding_date'], x['repo_id']), axis=1)

2011-02-19 01:58:42 3
2012-04-19 19:45:52 8
2012-04-19 19:45:52 8
2012-04-19 19:45:52 8
2012-04-19 19:45:52 8
2012-04-19 19:45:52 8
2012-04-19 19:45:52 8
2012-04-19 19:45:52 8
2012-04-19 19:45:52 8
2009-01-05 13:00:43 19
2012-05-14 19:37:26 19
2012-06-07 01:38:45 19
2015-10-21 18:50:41 19
2015-12-07 17:40:27 19
2013-06-18 17:54:10 19
2009-01-05 13:00:43 19
2013-04-04 16:57:25 19
2009-01-05 13:00:43 19
2020-06-17 19:28:17 19
2020-06-05 14:53:56 19
2011-09-08 14:52:50 34
2010-03-05 02:31:28 37
2010-01-05 23:34:37 37
2010-01-05 23:34:37 37
2010-11-10 00:14:25 37
2010-01-05 23:34:37 37
2010-01-05 23:34:37 37
2011-08-11 08:03:08 37
2010-01-05 23:34:37 37
2010-01-05 23:34:37 37
2011-04-28 14:10:23 37
2010-01-05 23:34:37 37
2010-01-05 23:34:37 37
2010-09-25 17:09:11 37
2010-01-05 23:34:37 37
2010-01-05 23:34:37 37
2011-04-05 21:45:40 37
2010-01-05 23:34:37 37
2010-01-05 23:34:37 37
2010-01-05 23:34:37 37
2010-01-05 23:34:37 37
2010-12-02 05:46:29 37
2016-10-05 20:38:11 37
2010-01-05 23:34:37 

# Last onboarding

In [38]:
# df_onboardings = pd.read_csv('onboarding_old.csv')

# repos = df_onboardings['repo_id'].unique()

# df_project_members = pd.read_csv(join(path,"project_members.csv"), names=["repo_id", "user_id", "created_at"])

df_project_members = df_project_members[df_project_members['repo_id'].isin(repos)]

# df_project_members['created_at'] = pd.to_datetime(df_project_members['created_at'])

In [39]:
def get_last_member(date, project, user_id):
    this_project_members_before_integration = df_project_members.loc[(df_project_members['created_at'] < pd.to_datetime(date)) & (df_project_members['repo_id'] == project) & (df_project_members['user_id'] != user_id)]
    return this_project_members_before_integration['created_at'].max()

In [40]:
df_onboardings["last_member"] = df_onboardings.apply(lambda x: get_last_member(x['onboarding_date'], x['repo_id'], x['user_id']), axis=1)

In [45]:
df_onboardings.to_csv('onboarding_after_calc_last_member.csv')

# Project Details

In [ ]:
unique_projects = df_onboardings['repo_id'].unique()
projects = []


chunk_projects = pd.read_csv(join(path, "projects.csv"), index_col=False, chunksize=5000000  ,escapechar='\\', header=None, sep=",", quotechar='"',encoding="utf-8", names=["id", "url", "owner_id", "name", "descriptor", "language", "created_at", "forked_from", "deleted", "updated_at"], na_values="not available", on_bad_lines="warn") #, engine="python")

i=0
for chunk in chunk_projects:
    print("chunk ", i)
    projects.append(chunk[chunk['id'].isin(unique_projects)])
    i += 1

df_projects = pd.concat(projects)

In [47]:
df_onboarding_x_projects = df_onboardings.merge(df_projects[['id', 'owner_id', 'language', 'created_at']], left_on='repo_id', right_on='id', suffixes=['', '_project'])

df_onboardings['project_author_id'] = df_onboarding_x_projects['owner_id']
df_onboardings['project_language'] = df_onboarding_x_projects['language']
df_onboardings['project_created_at'] = df_onboarding_x_projects['created_at']

# First Onboarding

In [ ]:
# df_onboardings = pd.read_csv('df_onboardings.csv', index_col=0)

# repos = df_onboardings['repo_id'].unique()

# df_project_members = pd.read_csv(join(path,"project_members.csv"), names=["repo_id", "user_id", "created_at"])

# df_project_members = df_project_members[df_project_members['repo_id'].isin(repos)]

# df_project_members['created_at'] = pd.to_datetime(df_project_members['created_at'])

In [9]:
def get_first_member(date, project, user_id):
    this_project_members_before_integration = df_project_members.loc[(df_project_members['created_at'] < pd.to_datetime(date)) & (df_project_members['repo_id'] == project) & (df_project_members['user_id'] != user_id)]
    return this_project_members_before_integration['created_at'].min()

In [10]:
df_onboardings["first_member"] = df_onboardings.apply(lambda x: get_first_member(x['onboarding_date'], x['repo_id'], x['project_author_id']), axis=1)


# Calculando o delta

In [14]:
df_onboardings['delta_project_creation'] = pd.to_datetime(df_onboardings['onboarding_date']) - pd.to_datetime(df_onboardings['project_created_at'])

df_onboardings['delta_first_onboarding'] = pd.to_datetime(df_onboardings['onboarding_date']) - pd.to_datetime(df_onboardings['first_member'])

df_onboardings['delta_last_onboarding'] = pd.to_datetime(df_onboardings['onboarding_date']) - pd.to_datetime(df_onboardings['last_member'])

df_onboardings['delta_first_commit'] = pd.to_datetime(df_onboardings['onboarding_date']) - pd.to_datetime(df_onboardings['first_commit'])

df_onboardings['delta_last_commit'] = pd.to_datetime(df_onboardings['onboarding_date']) - pd.to_datetime(df_onboardings['last_commit'])


In [15]:
df_onboardings.to_csv('df_onboardings.csv')

# getting date from project_members

In [4]:
df_onboardings = pd.read_csv('df_onboardings.csv', index_col=0)

repos = df_onboardings['repo_id'].unique()

df_project_members = pd.read_csv(join(path,"project_members.csv"), names=["repo_id", "user_id", "created_at"])

df_project_members = df_project_members[df_project_members['repo_id'].isin(repos)]

df_project_members['created_at'] = pd.to_datetime(df_project_members['created_at'])

In [5]:
df_test = df_onboardings.merge(df_project_members, left_on=['repo_id', 'user_id'], right_on=['repo_id', 'user_id'],  how='left', suffixes=['_members', '_onb'])


In [7]:
df_test.loc[df_test['onboarding_date'] != df_test['created_at']]

Empty DataFrame
Columns: [repo_id, user_id, onboarding_date, total_commits, first_commit, last_commit, project_members, last_member, project_author_id, project_language, project_created_at, first_member, delta_project_creation, delta_first_onboarding, delta_last_onboarding, delta_first_commit, delta_last_commit, created_at]
Index: []